In [1]:
import os
import glob
import pandas as pd

cwd = os.getcwd()

file_path = glob.glob(os.path.join(cwd, 'dataset', '2016_Building_Energy_Benchmarking.csv'))[0]
df = pd.read_csv(file_path)

df = df[(df['ComplianceStatus'] == 'Compliant') & (df['Outlier'].isna())]

# Filter the DataFrame to keep only rows where BuildingType is "NonResidential", "Nonresidential COS", or "Nonresidential WA"
df = df[df['BuildingType'].isin(['NonResidential', 'Nonresidential COS', 'Nonresidential WA'])]


df.head()


OSEBuildingID  DataYear    BuildingType PrimaryPropertyType  \
0              1      2016  NonResidential               Hotel   
1              2      2016  NonResidential               Hotel   
2              3      2016  NonResidential               Hotel   
3              5      2016  NonResidential               Hotel   
4              8      2016  NonResidential               Hotel   

                  PropertyName          Address     City State  ZipCode  \
0         Mayflower park hotel    405 Olive way  Seattle    WA  98101.0   
1              Paramount Hotel  724 Pine street  Seattle    WA  98101.0   
2      5673-The Westin Seattle  1900 5th Avenue  Seattle    WA  98101.0   
3                    HOTEL MAX   620 STEWART ST  Seattle    WA  98101.0   
4  WARWICK SEATTLE HOTEL (ID8)    401 LENORA ST  Seattle    WA  98121.0   

  TaxParcelIdentificationNumber  ...  Electricity(kWh) Electricity(kBtu)  \
0                    0659000030  ...      1.156514e+06         3946027.0   
1                    0659000220  ...      9.504252e+05         3242851.0   
2                    0659000475  ...      1.451544e+07        49526664.0   
3                    0659000640  ...      8.115253e+05         2768924.0   
4                    0659000970  ...      1.573449e+06         5368607.0   

   NaturalGas(therms)  NaturalGas(kBtu)  DefaultData  Comments  \
0         12764.52930         1276453.0        False       NaN   
1         51450.81641         5145082.0        False       NaN   
2         14938.00000         1493800.0        False       NaN   
3         18112.13086         1811213.0        False       NaN   
4         88039.98438         8803998.0        False       NaN   

   ComplianceStatus  Outlier  TotalGHGEmissions  GHGEmissionsIntensity  
0         Compliant      NaN             249.98                   2.83  
1         Compliant      NaN             295.86                   2.86  
2         Compliant      NaN            2089.28                   2.19  
3         Compliant      NaN             286.43                   4.67  
4         Compliant      NaN             505.01                   2.88  

[5 rows x 46 columns]

In [2]:
def drop_columns_by_nan_threshold(df, threshold):
    nan_percentage = df.isna().mean() * 100
    cols_to_drop = nan_percentage[nan_percentage > threshold].index.tolist()
    df_dropped = df.drop(columns=cols_to_drop)
    dropped_columns_info = {col: nan_percentage[col] for col in cols_to_drop}
    print(f"Dropped columns: {dropped_columns_info}")
    return df_dropped

def drop_columns_by_value_threshold(df, threshold):
    cols_to_drop = []
    dropped_columns_info = {}

    for col in df.columns:
        value_counts = df[col].value_counts(normalize=True) * 100
        if not value_counts.empty and value_counts.iloc[0] > threshold:
            cols_to_drop.append(col)
            top_values = value_counts.head(3).to_dict()
            dropped_columns_info[col] = top_values

    df_dropped = df.drop(columns=cols_to_drop)
    print(f"Dropped columns: {dropped_columns_info}")
    return df_dropped

def check_uniqueness(df):
    unique_checks = [
        (['OSEBuildingID'], "OSEBuildingID is unique"),
        (['PropertyName', 'Address'], "Couple (PropertyName, Address) is unique"),
        (['CouncilDistrictCode', 'Neighborhood'], "Combination (CouncilDistrictCode, Neighborhood) has unique ZipCode")
    ]
    
    for columns, message in unique_checks:
        if df[columns].duplicated(keep=False).any():
            duplicates = df[df.duplicated(subset=columns, keep=False)]
            return duplicates[columns + ['ZipCode']]
    
    return "All checks passed"

threshold_nan = 85
df_cleaned = drop_columns_by_nan_threshold(df, threshold_nan)

threshold_unique_value = 99
df_cleaned = drop_columns_by_value_threshold(df_cleaned, threshold_unique_value)



result = check_uniqueness(df_cleaned)

df_cleaned.set_index('OSEBuildingID', inplace=True)

if isinstance(result, str):
    display(df_cleaned.head())
else:
    print(result)



Dropped columns: {'YearsENERGYSTARCertified': np.float64(93.9894319682959), 'Comments': np.float64(100.0), 'Outlier': np.float64(100.0)}
Dropped columns: {'DataYear': {2016: 100.0}, 'City': {'Seattle': 99.93394980184941, 'Seatt2le': 0.06605019815059446}, 'State': {'WA': 100.0}, 'DefaultData': {False: 100.0}, 'ComplianceStatus': {'Compliant': 100.0}}
      CouncilDistrictCode           Neighborhood  ZipCode
0                       7               DOWNTOWN  98101.0
1                       7               DOWNTOWN  98101.0
2                       7               DOWNTOWN  98101.0
3                       7               DOWNTOWN  98101.0
4                       7               DOWNTOWN  98121.0
...                   ...                    ...      ...
3368                    3                CENTRAL      NaN
3372                    2               DOWNTOWN      NaN
3373                    7  MAGNOLIA / QUEEN ANNE      NaN
3374                    1       GREATER DUWAMISH      NaN
3375      

In [3]:
import numpy as np
import pandas as pd
import plotly.express as px
from scipy.stats import chi2_contingency

def identify_categorical_columns(df):
    return df.select_dtypes(include=['object', 'category']).columns.tolist()

def fill_missing_categorical(df, columns, placeholder='missing'):
    df_filled = df.copy()
    for column in columns:
        df_filled[column] = df_filled[column].fillna(placeholder)
    return df_filled

def cramers_v(confusion_matrix):
    chi2 = chi2_contingency(confusion_matrix)[0]
    n = confusion_matrix.values.sum()  
    phi2 = chi2 / n
    r, k = confusion_matrix.shape
    phi2corr = max(0, phi2 - ((k-1)*(r-1))/(n-1))
    rcorr = r - ((r-1)**2)/(n-1)
    kcorr = k - ((k-1)**2)/(n-1)
    return np.sqrt(phi2corr / min((kcorr-1), (rcorr-1)))

def calculate_cramers_v_matrix(df, columns):
    cramers_v_matrix = pd.DataFrame(index=columns, columns=columns)
    for col1 in columns:
        for col2 in columns:
            if col1 == col2:
                cramers_v_matrix.loc[col1, col2] = 1.0
            else:
                confusion_matrix = pd.crosstab(df[col1], df[col2])
                cramers_v_matrix.loc[col1, col2] = cramers_v(confusion_matrix)
    return cramers_v_matrix.astype(float)

def plot_cramers_v_matrix(cramers_v_matrix):
    mask = np.triu(np.ones_like(cramers_v_matrix, dtype=bool))
    cramers_v_matrix_masked = cramers_v_matrix.mask(mask)
    
    fig = px.imshow(cramers_v_matrix_masked, text_auto=True, aspect="auto", color_continuous_scale='Blues')
    fig.update_layout(title='Cramér\'s V Matrix (Upper Triangle)', xaxis_title='Features', yaxis_title='Features')
    fig.show()

# Cast all columns that are not already strings to strings
def cast_all_columns_to_string(df):
    for col in df.columns:
        if df[col].dtype != 'object':
            df[col] = df[col].astype(str)
    return df

# Filter out columns with only one unique value
def filter_single_value_columns(df):
    return [col for col in df.columns if df[col].nunique() > 1]


# Cast to string
df_cramer = cast_all_columns_to_string(df_cleaned)

# Identify categorical columns
categorical_columns = identify_categorical_columns(df_cramer)
print("Categorical Columns:", categorical_columns)

# Fill missing values in categorical columns
df_cramer = fill_missing_categorical(df_cramer, categorical_columns)
print("Filled DataFrame Columns:", df_cramer.columns)

df_cramer = df_cramer.drop(columns=['SiteEnergyUse(kBtu)'])

# Filter out columns with only one unique value
filtered_columns = filter_single_value_columns(df_cramer)
print("Filtered Columns:", filtered_columns)

# Calculate Cramér's V matrix
cramers_v_matrix = calculate_cramers_v_matrix(df_cramer, filtered_columns)
print("Cramér's V Matrix Columns:", cramers_v_matrix.columns)

# Plot Cramér's V matrix
plot_cramers_v_matrix(cramers_v_matrix)

def get_highly_correlated_features(cramers_v_matrix, threshold=0.8):
    correlated_features = []
    for col in cramers_v_matrix.columns:
        high_corr = cramers_v_matrix[col][cramers_v_matrix[col] > threshold]
        high_corr = high_corr[high_corr.index != col]
        for index, value in high_corr.items():
            correlated_features.append((col, index, value))
    return correlated_features

# Get highly correlated features
threshold = 0.8
highly_correlated_features = get_highly_correlated_features(cramers_v_matrix, threshold)

print("Highly correlated features (above threshold):")
for feature1, feature2, value in highly_correlated_features:
    print(f"{feature1} and {feature2}: {value}")

Categorical Columns: ['BuildingType', 'PrimaryPropertyType', 'PropertyName', 'Address', 'ZipCode', 'TaxParcelIdentificationNumber', 'CouncilDistrictCode', 'Neighborhood', 'Latitude', 'Longitude', 'YearBuilt', 'NumberofBuildings', 'NumberofFloors', 'PropertyGFATotal', 'PropertyGFAParking', 'PropertyGFABuilding(s)', 'ListOfAllPropertyUseTypes', 'LargestPropertyUseType', 'LargestPropertyUseTypeGFA', 'SecondLargestPropertyUseType', 'SecondLargestPropertyUseTypeGFA', 'ThirdLargestPropertyUseType', 'ThirdLargestPropertyUseTypeGFA', 'ENERGYSTARScore', 'SiteEUI(kBtu/sf)', 'SiteEUIWN(kBtu/sf)', 'SourceEUI(kBtu/sf)', 'SourceEUIWN(kBtu/sf)', 'SiteEnergyUse(kBtu)', 'SiteEnergyUseWN(kBtu)', 'SteamUse(kBtu)', 'Electricity(kWh)', 'Electricity(kBtu)', 'NaturalGas(therms)', 'NaturalGas(kBtu)', 'TotalGHGEmissions', 'GHGEmissionsIntensity']
Filled DataFrame Columns: Index(['BuildingType', 'PrimaryPropertyType', 'PropertyName', 'Address',
       'ZipCode', 'TaxParcelIdentificationNumber', 'CouncilDistrict

Highly correlated features (above threshold):
PrimaryPropertyType and ListOfAllPropertyUseTypes: 0.82388835379073
PrimaryPropertyType and LargestPropertyUseType: 0.8879255751736073
Address and TaxParcelIdentificationNumber: 0.8767206459443952
Address and Latitude: 0.929467106741811
Address and Longitude: 0.8997886186650066
ZipCode and CouncilDistrictCode: 0.8314457922948185
TaxParcelIdentificationNumber and Address: 0.876720645944364
CouncilDistrictCode and ZipCode: 0.8314457922948185
CouncilDistrictCode and Neighborhood: 0.8628216017308712
Neighborhood and CouncilDistrictCode: 0.8628216017308713
Latitude and Address: 0.9294671067417932
Longitude and Address: 0.8997886186649883
PropertyGFATotal and PropertyGFABuilding(s): 0.9925593722263624
PropertyGFABuilding(s) and PropertyGFATotal: 0.9925593722263624
ListOfAllPropertyUseTypes and PrimaryPropertyType: 0.82388835379073
ListOfAllPropertyUseTypes and LargestPropertyUseType: 0.8566472509201843
ListOfAllPropertyUseTypes and SecondLargestP

In [4]:
import pandas as pd
import numpy as np
import plotly.express as px

# Function to check if ListOfAllPropertyUseTypes equals LargestPropertyUseType
def check_all_vs_largest(df):
    temp_df = df.copy()
    discrepancies = []
    for index, row in temp_df.iterrows():
        if pd.isna(row['LargestPropertyUseType']):
            temp_df.at[index, 'LargestPropertyUseType'] = row['ListOfAllPropertyUseTypes']
        elif row['ListOfAllPropertyUseTypes'] != row['LargestPropertyUseType']:
            discrepancies.append((index, row['ListOfAllPropertyUseTypes'], row['LargestPropertyUseType']))
    if discrepancies:
        return pd.DataFrame(discrepancies, columns=['Index', 'ListOfAllPropertyUseTypes', 'LargestPropertyUseType']), temp_df
    else:
        return "No discrepancies found in ListOfAllPropertyUseTypes vs LargestPropertyUseType.", temp_df

# Function to check if PropertyGFATotal equals the sum of PropertyGFAParking and PropertyGFABuilding(s)
def check_gfa_total(df):
    temp_df = df.copy()
    discrepancies = []
    for index, row in temp_df.iterrows():
        if pd.notna(row['PropertyGFATotal']) and pd.notna(row['PropertyGFAParking']) and pd.notna(row['PropertyGFABuilding(s)']):
            # Convert relevant columns to numeric
            property_gfa_total = pd.to_numeric(row['PropertyGFATotal'], errors='coerce')
            property_gfa_parking = pd.to_numeric(row['PropertyGFAParking'], errors='coerce')
            property_gfa_building = pd.to_numeric(row['PropertyGFABuilding(s)'], errors='coerce')
            if property_gfa_total != property_gfa_parking + property_gfa_building:
                discrepancies.append((index, property_gfa_total, property_gfa_parking, property_gfa_building))
    if discrepancies:
        return pd.DataFrame(discrepancies, columns=['Index', 'PropertyGFATotal', 'PropertyGFAParking', 'PropertyGFABuilding(s)']), temp_df
    else:
        return "No discrepancies found in PropertyGFATotal.", temp_df

# Function to check if ListOfAllPropertyUseTypes contains all non-null LargestPropertyUseType, SecondLargestPropertyUseType, and ThirdLargestPropertyUseType
def check_list_of_all_property_use_types(df):
    temp_df = df.copy()
    discrepancies = []
    for index, row in temp_df.iterrows():
        # Remove "Parking" from ListOfAllPropertyUseTypes
        list_of_all_property_use_types = row['ListOfAllPropertyUseTypes'].replace('Parking, ', '').replace(', Parking', '').replace('Parking', '')
        
        property_use_types = [row['LargestPropertyUseType'], row['SecondLargestPropertyUseType'], row['ThirdLargestPropertyUseType']]
        property_use_types = [ptype for ptype in property_use_types if pd.notna(ptype) and ptype != 'Parking']
        
        # Check if all property use types are in ListOfAllPropertyUseTypes
        missing_types = [ptype for ptype in property_use_types if ptype not in list_of_all_property_use_types]
        
        if missing_types:
            discrepancies.append((index, row['ListOfAllPropertyUseTypes'], ', '.join(missing_types)))
    
    if discrepancies:
        return pd.DataFrame(discrepancies, columns=['Index', 'ListOfAllPropertyUseTypes', 'MissingTypes']), temp_df
    else:
        return "No discrepancies found in ListOfAllPropertyUseTypes.", temp_df

# Function to check if PropertyGFABuilding(s) is within ±20% of the sum of LargestPropertyUseTypeGFA, SecondLargestPropertyUseTypeGFA, and ThirdLargestPropertyUseTypeGFA
def check_gfa_building(df, std_threshold=2):
    temp_df = df.copy()
    discrepancies = []
    percentage_diffs = []
    outliers = []
    
    for index, row in temp_df.iterrows():
        # Check for "Parking" in any of the property use types and set corresponding values to 0
        if 'Parking' in [row['LargestPropertyUseType'], row['SecondLargestPropertyUseType'], row['ThirdLargestPropertyUseType']]:
            if row['LargestPropertyUseType'] == 'Parking':
                temp_df.at[index, 'LargestPropertyUseType'] = np.nan
                temp_df.at[index, 'LargestPropertyUseTypeGFA'] = 0
            if row['SecondLargestPropertyUseType'] == 'Parking':
                temp_df.at[index, 'SecondLargestPropertyUseType'] = np.nan
                temp_df.at[index, 'SecondLargestPropertyUseTypeGFA'] = 0
            if row['ThirdLargestPropertyUseType'] == 'Parking':
                temp_df.at[index, 'ThirdLargestPropertyUseType'] = np.nan
                temp_df.at[index, 'ThirdLargestPropertyUseTypeGFA'] = 0
        
        if pd.notna(temp_df.at[index, 'PropertyGFABuilding(s)']):
            # Convert relevant columns to numeric and replace NaN values with 0
            property_gfa_building = pd.to_numeric(temp_df.at[index, 'PropertyGFABuilding(s)'], errors='coerce')
            largest_gfa = pd.to_numeric(temp_df.at[index, 'LargestPropertyUseTypeGFA'], errors='coerce')
            second_largest_gfa = pd.to_numeric(temp_df.at[index, 'SecondLargestPropertyUseTypeGFA'], errors='coerce')
            third_largest_gfa = pd.to_numeric(temp_df.at[index, 'ThirdLargestPropertyUseTypeGFA'], errors='coerce')
            
            # Replace NaN values with 0
            largest_gfa = 0 if pd.isna(largest_gfa) else largest_gfa
            second_largest_gfa = 0 if pd.isna(second_largest_gfa) else second_largest_gfa
            third_largest_gfa = 0 if pd.isna(third_largest_gfa) else third_largest_gfa
            
            total_gfa = largest_gfa + second_largest_gfa + third_largest_gfa
            
            # Calculate percentage difference
            if total_gfa != 0:
                percentage_diff = ((property_gfa_building - total_gfa) / total_gfa) * 100
                percentage_diffs.append((index, percentage_diff))
                
                # Identify outliers based on the standard deviation threshold
                mean_diff = np.mean([diff for _, diff in percentage_diffs])
                std_diff = np.std([diff for _, diff in percentage_diffs])
                if abs(percentage_diff - mean_diff) > std_threshold * std_diff:
                    outliers.append((index, percentage_diff))
                else:
                    discrepancies.append((index, property_gfa_building, total_gfa))
    
    # Plot the percentage differences
    percentage_diff_values = [diff for _, diff in percentage_diffs]
    fig = px.histogram(percentage_diff_values, nbins=50, marginal="box", title="Percentage Difference between PropertyGFABuilding(s) and TotalGFA")
    fig.update_layout(xaxis_title="Percentage Difference", yaxis_title="Count")
    fig.show()
    
    # Show outliers
    outliers_df = pd.DataFrame(outliers, columns=['Index', 'Percentage Difference'])
    print("Outliers:")
    print(outliers_df)
    
    # Drop outliers from temp_df
    outlier_indices = [index for index, _ in outliers]
    temp_df = temp_df.drop(outlier_indices)
    
    if discrepancies:
        return pd.DataFrame(discrepancies, columns=['Index', 'PropertyGFABuilding(s)', 'TotalGFA']), temp_df
    else:
        return "No discrepancies found in PropertyGFABuilding(s).", temp_df

# Function to calculate BuildingTotalSurface and ratios
def calculate_surface_and_ratios(df):
    # Ensure relevant columns are numeric
    df['LargestPropertyUseTypeGFA'] = pd.to_numeric(df['LargestPropertyUseTypeGFA'], errors='coerce').fillna(0)
    df['SecondLargestPropertyUseTypeGFA'] = pd.to_numeric(df['SecondLargestPropertyUseTypeGFA'], errors='coerce').fillna(0)
    df['ThirdLargestPropertyUseTypeGFA'] = pd.to_numeric(df['ThirdLargestPropertyUseTypeGFA'], errors='coerce').fillna(0)
    
    df['BuildingTotalSurface'] = df['LargestPropertyUseTypeGFA'] + df['SecondLargestPropertyUseTypeGFA'] + df['ThirdLargestPropertyUseTypeGFA']
    
    df['LargestSurfaceRatio'] = df['LargestPropertyUseTypeGFA'] / df['BuildingTotalSurface']
    df['SecondSurfaceRatio'] = df['SecondLargestPropertyUseTypeGFA'] / df['BuildingTotalSurface']
    df['ThirdSurfaceRatio'] = df['ThirdLargestPropertyUseTypeGFA'] / df['BuildingTotalSurface']
    
    return df

# Check each case
all_vs_largest_discrepancies, temp_df_primary_vs_largest = check_all_vs_largest(df_cleaned)
gfa_total_discrepancies, temp_df_gfa_total = check_gfa_total(temp_df_primary_vs_largest)
list_of_all_property_use_types_discrepancies, temp_df_list_of_all_property_use_types = check_list_of_all_property_use_types(temp_df_gfa_total)
gfa_building_discrepancies, temp_df_gfa_building = check_gfa_building(temp_df_list_of_all_property_use_types)

# Calculate BuildingTotalSurface and ratios
temp_df_gfa_building = calculate_surface_and_ratios(temp_df_gfa_building)

# Display results
print("All vs Largest Property Use Type Discrepancies:")
print(all_vs_largest_discrepancies)

print("\nProperty GFA Total Discrepancies:")
print(gfa_total_discrepancies)

print("\nList of All Property Use Types Discrepancies:")
print(list_of_all_property_use_types_discrepancies)

print("\nGFA Building Discrepancies:")
print(gfa_building_discrepancies)

print("\nDataFrame with BuildingTotalSurface and Ratios:")
print(temp_df_gfa_building[['BuildingTotalSurface', 'LargestSurfaceRatio', 'SecondSurfaceRatio', 'ThirdSurfaceRatio']])

Outliers:
    Index  Percentage Difference
0       9             -32.353934
1      24              37.814239
2      38              37.630711
3      41             320.804576
4     572              66.666667
..    ...                    ...
59  40034             -65.566023
60  49699             -84.440276
61  49865             -80.591924
62  49872             132.414356
63  49940             -62.929113

[64 rows x 2 columns]
All vs Largest Property Use Type Discrepancies:
     Index                          ListOfAllPropertyUseTypes  \
0        2                         Hotel, Parking, Restaurant   
1        8                      Hotel, Parking, Swimming Pool   
2       18                                     Hotel, Parking   
3       19                                     Hotel, Parking   
4       21                      Data Center, Library, Parking   
..     ...                                                ...   
821  50208  Fitness Center/Health Club/Gym, Office, Other ...   
822

In [5]:
# Drop specified columns
columns_to_drop = ['BuildingType','PropertyName', 'Address', 'Neighborhood', 'ZipCode', 'PrimaryPropertyType','Electricity(kWh)','NaturalGas(therms)','ListOfAllPropertyUseTypes',
'PropertyGFATotal','PropertyGFABuilding(s)','SiteEUI(kBtu/sf)','SiteEUIWN(kBtu/sf)','SourceEUI(kBtu/sf)','SourceEUIWN(kBtu/sf)',
'SiteEnergyUseWN(kBtu)','SiteEnergyUse(kBtu)','TaxParcelIdentificationNumber']


def clean_df(df):
    temp_df = df.copy()
    
    # Replace NaN values with 0 for numeric columns and convert to float64
    temp_df['LargestPropertyUseTypeGFA'] = temp_df['LargestPropertyUseTypeGFA'].fillna(0.0).astype(float)
    temp_df['SecondLargestPropertyUseTypeGFA'] = temp_df['SecondLargestPropertyUseTypeGFA'].fillna(0).astype(float)
    temp_df['ThirdLargestPropertyUseTypeGFA'] = temp_df['ThirdLargestPropertyUseTypeGFA'].fillna(0).astype(float)
    temp_df['PropertyGFAParking'] = temp_df['PropertyGFAParking'].fillna(0).astype(float)
    
    # Replace NaN values with 'None' for string columns
    temp_df['LargestPropertyUseType'] = temp_df['LargestPropertyUseType'].fillna('None')
    temp_df['SecondLargestPropertyUseType'] = temp_df['SecondLargestPropertyUseType'].fillna('None')
    temp_df['ThirdLargestPropertyUseType'] = temp_df['ThirdLargestPropertyUseType'].fillna('None')
    
    # Replace NaN values with 0 for energy columns and convert to float64
    temp_df['SteamUse(kBtu)'] = temp_df['SteamUse(kBtu)'].fillna(0).astype(float)
    temp_df['Electricity(kBtu)'] = temp_df['Electricity(kBtu)'].fillna(0).astype(float)
    temp_df['NaturalGas(kBtu)'] = temp_df['NaturalGas(kBtu)'].fillna(0).astype(float)
    
    # Create TotalEnergy(kBtu) feature
    temp_df['TotalEnergy(kBtu)'] = temp_df['SteamUse(kBtu)'] + temp_df['Electricity(kBtu)'] + temp_df['NaturalGas(kBtu)']
    
    # Create percentage columns
    temp_df['SteamUse'] = (temp_df['SteamUse(kBtu)'] / temp_df['TotalEnergy(kBtu)']) * 100
    temp_df['Electricity'] = (temp_df['Electricity(kBtu)'] / temp_df['TotalEnergy(kBtu)']) * 100
    temp_df['NaturalGas'] = (temp_df['NaturalGas(kBtu)'] / temp_df['TotalEnergy(kBtu)']) * 100
    
    # Drop original energy columns
    temp_df = temp_df.drop(columns=['SteamUse(kBtu)', 'Electricity(kBtu)', 'NaturalGas(kBtu)'])
    
    # Ensure the target variables are numeric
    temp_df['TotalEnergy(kBtu)'] = pd.to_numeric(temp_df['TotalEnergy(kBtu)'], errors='coerce')
    temp_df['TotalGHGEmissions'] = pd.to_numeric(temp_df['TotalGHGEmissions'], errors='coerce')
    temp_df['GHGEmissionsIntensity'] = pd.to_numeric(temp_df['GHGEmissionsIntensity'], errors='coerce')
    temp_df['YearBuilt'] = pd.to_numeric(temp_df['YearBuilt'], errors='coerce')
    temp_df['CouncilDistrictCode'] = pd.to_numeric(temp_df['CouncilDistrictCode'], errors='coerce')
    temp_df['NumberofBuildings'] = pd.to_numeric(temp_df['NumberofBuildings'], errors='coerce')
    temp_df['NumberofFloors'] = pd.to_numeric(temp_df['NumberofFloors'], errors='coerce')
    temp_df['ENERGYSTARScore'] = pd.to_numeric(temp_df['ENERGYSTARScore'], errors='coerce')

    # Drop specified columns
    temp_df = temp_df.drop(columns=columns_to_drop)

    return temp_df

# Example usage
df_cleaned_value = clean_df(temp_df_gfa_building)

In [6]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.impute import SimpleImputer



# Function to create box plots for a given target variable
def create_box_plots(df, target):
    df_temp = df.copy()

    # Identify categorical and numerical columns
    categorical_cols = df_temp.select_dtypes(include=['object']).columns.tolist()
    numerical_cols = df_temp.select_dtypes(include=['number']).columns.tolist()


    # Label encode categorical columns
    label_encoders = {col: LabelEncoder().fit(df_temp[col]) for col in categorical_cols}
    for col, le in label_encoders.items():
        df_temp[col] = le.transform(df_temp[col])

    # Create a column transformer for preprocessing
    preprocessor = ColumnTransformer(
        transformers=[
            ('num', Pipeline(steps=[
                ('imputer', SimpleImputer(strategy='median'))
            ]), numerical_cols),
            ('cat', Pipeline(steps=[
                ('imputer', SimpleImputer(strategy='most_frequent')),
                ('scaler', StandardScaler())
            ]), categorical_cols)
        ]
    )
    
    # Apply the preprocessing pipeline
    preprocessed_data = preprocessor.fit_transform(df_temp)
    
    # Combine numerical and categorical feature names
    feature_names = numerical_cols + categorical_cols
    
    # Convert the preprocessed data to a DataFrame
    preprocessed_df = pd.DataFrame(preprocessed_data, columns=feature_names)
    
    # Add the target variable back to the DataFrame
    preprocessed_df[target] = df_temp[target].values
    
    # Split the target variable into 10 quantiles
    preprocessed_df['y_quantile'] = pd.qcut(preprocessed_df[target], q=10, labels=False)
    
    # Create a single chart with toggle options
    fig = go.Figure()

    # Add box plots for each predictor and each quantile
    for predictor in feature_names:
        for quantile in range(10):
            quantile_data = preprocessed_df[preprocessed_df['y_quantile'] == quantile]
            max_value = quantile_data[target].max()
            min_value = quantile_data[target].min()
            fig.add_trace(go.Box(
                y=quantile_data[predictor],
                name=f'Q{quantile} {min_value} - {max_value}',
                boxmean=True,
                visible=False
            ))

    # Initially show the first predictor's box plots
    for i in range(10):
        fig.data[i].visible = True

    # Create buttons to toggle visibility of each predictor's box plots
    buttons = []
    for i, predictor in enumerate(feature_names):
        visibility = [False] * len(fig.data)
        for j in range(10):
            visibility[i * 10 + j] = True
        buttons.append(dict(
            method='update',
            label=predictor,
            args=[{'visible': visibility}]
        ))

    # Add a button to show all predictors
    all_visibility = [True] * len(fig.data)
    buttons.append(dict(
        method='update',
        label='All',
        args=[{'visible': all_visibility}]
    ))

    fig.update_layout(
        updatemenus=[dict(
            active=0,
            buttons=buttons,
            direction='down',
            showactive=True,
            x=0.5,  # Center the dropdown horizontally
            y=1.15  # Position the dropdown just below the title
        )],
        title=f'Normalized Box Plots of Predictors by Quantiles of {target}',
        xaxis_title='Quantiles of Target',
        yaxis_title='Normalized Values'
    )

    fig.show()

# Create box plots for each target variable
create_box_plots(df_cleaned_value, 'TotalEnergy(kBtu)')
create_box_plots(df_cleaned_value, 'TotalGHGEmissions')
create_box_plots(df_cleaned_value, 'GHGEmissionsIntensity')
create_box_plots(df_cleaned_value, 'ENERGYSTARScore')

In [7]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from pyproj import Transformer

# Define the transformer for latitude and longitude (WGS84) to UTM Zone 10N
transformer = Transformer.from_crs("epsg:4326", "epsg:32610", always_xy=True)
inverse_transformer = Transformer.from_crs("epsg:32610", "epsg:4326", always_xy=True)

# Seattle Center coordinates
seattle_center_lat = 47.620564
seattle_center_lon = -122.350616

# Function to transform coordinates
def transform_coordinates(df, lat_col='Latitude', lon_col='Longitude'):
    df_transformed = df.copy()
    
    # Transform the Seattle Center coordinates to UTM
    seattle_center_x, seattle_center_y = transformer.transform(seattle_center_lon, seattle_center_lat)
    
    # Transform the coordinates
    df_transformed['X'], df_transformed['Y'] = transformer.transform(
        df[lon_col].astype(float).values, 
        df[lat_col].astype(float).values
    )
    
    # Calculate the offset from Seattle Center
    df_transformed['X'] = df_transformed['X'] - seattle_center_x
    df_transformed['Y'] = df_transformed['Y'] - seattle_center_y
    
    return df_transformed

# Function to create the Plotly map
def create_plotly_map(df):
    # Transform the coordinates
    df_transformed = transform_coordinates(df)

    # Convert X/Y back to latitude/longitude for plotting
    #df_transformed['Transformed_Lon'], df_transformed['Transformed_Lat'] = inverse_transformer.transform(
    #   df_transformed['X'] + transformer.transform(seattle_center_lon, seattle_center_lat)[0],
    #   df_transformed['Y'] + transformer.transform(seattle_center_lon, seattle_center_lat)[1]
    #)

    # Ensure latitude and longitude columns are numeric
    df_transformed['Latitude'] = df_transformed['Latitude'].astype(float)
    df_transformed['Longitude'] = df_transformed['Longitude'].astype(float)

    # Create the figure
    fig = make_subplots()

    # List of plot configurations
    plot_configs = [
        {
            'name': 'GHG Emissions Intensity',
            'lat': df_transformed['Latitude'],
            'lon': df_transformed['Longitude'],
            'color': None,
            'size': 8,
            'color_column': df_transformed['GHGEmissionsIntensity'],
            'colorbar_title': 'GHG Emissions Intensity',
            'hover_text': df_transformed['GHGEmissionsIntensity'].astype(str)
        },
        {
            'name': 'Total Energy (kBtu)',
            'lat': df_transformed['Latitude'],
            'lon': df_transformed['Longitude'],
            'color': None,
            'size': 8,
            'color_column': df_transformed['TotalEnergy(kBtu)'],
            'colorbar_title': 'Total Energy (kBtu)',
            'hover_text': df_transformed['TotalEnergy(kBtu)'].astype(str)
        },
        {
            'name': 'Total GHG Emissions',
            'lat': df_transformed['Latitude'],
            'lon': df_transformed['Longitude'],
            'color': None,
            'size': 8,
            'color_column': df_transformed['TotalGHGEmissions'],
            'colorbar_title': 'Total GHG Emissions',
            'hover_text': df_transformed['TotalGHGEmissions'].astype(str)
        },
        {
            'name': 'ENERGYSTAR Score',
            'lat': df_transformed['Latitude'],
            'lon': df_transformed['Longitude'],
            'color': None,
            'size': 8,
            'color_column': df_transformed['ENERGYSTARScore'],
            'colorbar_title': 'ENERGYSTAR Score',
            'hover_text': df_transformed['ENERGYSTARScore'].astype(str)
        }
    ]

    # Add traces to the figure
    for i, config in enumerate(plot_configs):
        fig.add_trace(go.Scattermapbox(
            lat=config['lat'],
            lon=config['lon'],
            mode='markers',
            marker=dict(
                size=config['size'],
                color=config['color'] if config['color'] else config['color_column'],
                colorscale='RdYlGn_r' if config['color_column'] is not None else None,
                colorbar=dict(title=config['colorbar_title']) if config['color_column'] is not None else None
            ),
            name=config['name'],
            hovertext=config['hover_text'],
            hoverinfo='text',
            showlegend=False  # Hide legend entry for this trace
        ))

    # Update layout for the map
    fig.update_layout(
        mapbox=dict(
            style="open-street-map",
            center=dict(lat=47.620564, lon=-122.350616),
            zoom=12
        ),
        showlegend=False,  # Hide the legend
        updatemenus=[
            dict(
                type="buttons",
                direction="left",
                buttons=[
                    dict(
                        args=[{"visible": [i == j for j in range(len(plot_configs))]}],
                        label=config['name'],
                        method="update"
                    ) for i, config in enumerate(plot_configs)
                ],
                pad={"r": 8, "t": 8},
                showactive=True,
                x=0.2,
                xanchor="left",
                y=1.15,
                yanchor="top"
            ),
        ]
    )

    # Set the first trace to be visible by default
    fig.update_traces(visible=False)
    fig.data[0].visible = True

    fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

    fig.show()

    return df_transformed

# Example usage
# Assuming df_cleaned_value is your DataFrame
df_transformed = create_plotly_map(df_cleaned_value)

In [8]:
import pandas as pd
import numpy as np
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.model_selection import train_test_split, RepeatedKFold, GridSearchCV
from sklearn.linear_model import ElasticNet
from sklearn.svm import SVR
from sklearn.ensemble import GradientBoostingRegressor, RandomForestRegressor
from sklearn.metrics import mean_squared_error, r2_score, mean_absolute_error
from sklearn.preprocessing import StandardScaler, RobustScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer, KNNImputer
from sklearn.exceptions import NotFittedError


# Drop specified columns
columns_to_drop = ['CouncilDistrictCode', 'Latitude', 'Longitude', 'PropertyGFAParking', 'LargestPropertyUseTypeGFA', 'SecondLargestPropertyUseTypeGFA', 'ThirdLargestPropertyUseTypeGFA', 'GHGEmissionsIntensity']

df_ml = df_transformed.drop(columns=columns_to_drop)

# Define the target variables
targets = ['TotalEnergy(kBtu)', 'TotalGHGEmissions']

# Define the models and hyperparameters for GridSearchCV
models = {
    'ElasticNet': ElasticNet(random_state=42),
    'SVM': SVR(),
    'GradientBoosting': GradientBoostingRegressor(random_state=42),
    'RandomForest': RandomForestRegressor(random_state=42)
}

# Define the features and target variables
def define_features_and_target(df, target, targets):
    X = df.drop(columns=targets)
    y = df[target]
    return X, y

# Split the data into training and testing sets
def split_data(X, y):
    return train_test_split(X, y, test_size=0.2, random_state=42)



def create_production_pipeline(model, param_grid, X):
    categorical_cols = X.select_dtypes(include=['object']).columns.tolist()
    numerical_cols = X.select_dtypes(include=['number']).columns.tolist()
    

    try:
        preprocessor = ColumnTransformer(
            transformers=[
                ('num', Pipeline(steps=[
                    ('imputer', KNNImputer(n_neighbors=5)),
                    ('scaler', RobustScaler(quantile_range=(1.0, 99.0)))
                ]), numerical_cols),
                ('cat', Pipeline(steps=[
                    ('imputer', SimpleImputer(strategy='constant', fill_value='MISSING')),
                    ('onehot', OneHotEncoder(handle_unknown='ignore', sparse_output=False))
                ]), categorical_cols)
            ]
        )
        
        full_pipeline = Pipeline([
            ('preprocessor', preprocessor),
            ('model', model)
        ])
        
        cv = RepeatedKFold(n_splits=5, n_repeats=3, random_state=42)
        
        grid_search = GridSearchCV(
            full_pipeline,
            {f'model__{k}': v for k, v in param_grid.items()},
            cv=cv,
            scoring=['neg_mean_squared_error', 'r2', 'neg_mean_absolute_error'],
            refit='neg_mean_squared_error',
            n_jobs=-1,
            error_score='raise',
            verbose=1
        )
        
        return grid_search
        
    except Exception as e:
        print(f"Error in pipeline creation: {str(e)}")
        raise

# Update parameter grids
param_grids = {
    'ElasticNet': {
        'alpha': [0.01, 0.1, 1.0],
        'l1_ratio': [0.2, 0.5, 0.8],
        'max_iter': [5000],
        'tol': [1e-4]
    },
    'SVM': {
        'C': [0.1, 1, 10],
        'kernel': ['linear', 'rbf'],
        'gamma': ['scale', 'auto'],
        'epsilon': [0.1]
    },
    'GradientBoosting': {
        'n_estimators': [100, 200],
        'learning_rate': [0.01, 0.1],
        'max_depth': [3, 5],
        'subsample': [0.8, 1.0],
        'loss': ['squared_error']
    },
    'RandomForest': {
        'n_estimators': [100, 200],
        'max_depth': [10, 20],
        'min_samples_split': [2, 5],
        'max_features': ['log2', 'sqrt',None,0.5,0.8],
        'bootstrap': [True]
    }
}

# Rest of training code remains similar, just update the pipeline creation
best_models_dict = {}
X_train_dict = {}
X_test_dict = {}
y_train_dict = {}
y_test_dict = {}
all_cv_results_list = []
best_models = {}

for target in targets:
    X, y = define_features_and_target(df_ml, target, targets)
    X_train, X_test, y_train, y_test = split_data(X, y)
    
    best_models = {}
    all_cv_results = []
    
    for model_name, model in models.items():
        print(f"Training {model_name} for {target}...")
        grid_search = create_production_pipeline(model, param_grids[model_name], X_train)
        grid_search.fit(X_train, y_train)
        best_models[model_name] = grid_search.best_estimator_
        y_pred = grid_search.predict(X_test)
        
        mse = mean_squared_error(y_test, y_pred)
        rmse = np.sqrt(mse)
        mae = mean_absolute_error(y_test, y_pred)
        r2 = r2_score(y_test, y_pred)
        
        cv_results_df = pd.DataFrame(grid_search.cv_results_)
        cv_results_df['model'] = model_name
        all_cv_results.append(cv_results_df)
    
    best_models_dict[target] = best_models
    X_train_dict[target] = X_train
    X_test_dict[target] = X_test
    y_train_dict[target] = y_train
    y_test_dict[target] = y_test
    
    cv_results = pd.concat(all_cv_results, ignore_index=True)
    cv_results['target'] = target
    all_cv_results_list.append(cv_results)

all_cv_results_df = pd.concat(all_cv_results_list, ignore_index=True)


Training ElasticNet for TotalEnergy(kBtu)...
Fitting 15 folds for each of 9 candidates, totalling 135 fits
Training SVM for TotalEnergy(kBtu)...
Fitting 15 folds for each of 12 candidates, totalling 180 fits
Training GradientBoosting for TotalEnergy(kBtu)...
Fitting 15 folds for each of 16 candidates, totalling 240 fits
Training RandomForest for TotalEnergy(kBtu)...
Fitting 15 folds for each of 40 candidates, totalling 600 fits
Training ElasticNet for TotalGHGEmissions...
Fitting 15 folds for each of 9 candidates, totalling 135 fits
Training SVM for TotalGHGEmissions...
Fitting 15 folds for each of 12 candidates, totalling 180 fits
Training GradientBoosting for TotalGHGEmissions...
Fitting 15 folds for each of 16 candidates, totalling 240 fits
Training RandomForest for TotalGHGEmissions...
Fitting 15 folds for each of 40 candidates, totalling 600 fits


In [9]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import pandas as pd
import numpy as np

def format_feature_list(features, chunk_size=5):
    """Format feature list into chunks with line breaks"""
    chunks = [features[i:i + chunk_size] for i in range(0, len(features), chunk_size)]
    return '<br>'.join([', '.join(chunk) for chunk in chunks])

def get_feature_data(df, df_transformed, X_train_dict, target):
    """Get feature data for specific target"""
    return {
        'original_num': df.select_dtypes(include=['number']).columns.tolist(),
        'original_cat': df.select_dtypes(include=['object']).columns.tolist(),
        'new': [col for col in df_transformed.columns if col not in df.columns],
        'maintained': [col for col in df_transformed.columns if col in df.columns],
        'numerical': X_train_dict[target].select_dtypes(include=['number']).columns.tolist(),
        'categorical': X_train_dict[target].select_dtypes(include=['object']).columns.tolist()
    }

def create_sankey_nodes(features, models, best_models_dict, target, color_scheme):
    """Create nodes for Sankey diagram with proper color handling"""
    nodes_labels = []
    nodes_colors = []
    hover_data = []
    source = []
    target = []
    value = []
    
    # Define color scheme if not provided
    colors = color_scheme or {
        'primary': '#003f5c',
        'secondary': '#7a5195',
        'accent': '#ef5675',
        'stages': {
            'Raw Data': '#003f5c',
            'Features': '#7a5195',
            'Processing': '#ef5675',
            'Models': '#ffa600',
            'Output': '#ff7c43'
        },
        'preprocessing': '#66c2a5',
        'models': '#fc8d62',
        'new_features': '#ffa600'
    }

    # Main stages
    stages = [
        ('Raw Data', f"{len(features['original_num'] + features['original_cat'])}", "Original features"),
        ('Features', 'Engineering', "Feature creation"),
        ('Processing', 'Transform', "Data preprocessing"),
        ('Models', f"{len(models)}", "Model evaluation"),
        ('Output', 'Metrics', "Performance")
    ]
    
    # Add main stages
    stage_idx = 0
    for stage, info, hover in stages:
        nodes_labels.append(f"{stage}<br>{info}")
        nodes_colors.append(colors['stages'].get(stage, colors['primary'])) 
        hover_data.append(hover)
        if stage_idx > 0:
            source.append(stage_idx-1)
            target.append(stage_idx)
            value.append(1.0)
        stage_idx += 1
    
    # Add split nodes
    base_idx = len(nodes_labels)
    nodes_labels.extend([
        f"Raw Numerical<br>{len(features['original_num'])}",
        f"Raw Categorical<br>{len(features['original_cat'])}"
    ])
    hover_data.extend([
        f"Original numerical:<br>{format_feature_list(features['original_num'])}",
        f"Original categorical:<br>{format_feature_list(features['original_cat'])}"
    ])
    nodes_colors.extend([colors['preprocessing']] * 2)
    source.extend([0, 0])
    target.extend([base_idx, base_idx + 1])
    value.extend([0.5, 0.5])
    
    # Add engineering nodes
    eng_idx = len(nodes_labels)
    nodes_labels.extend([
        f"New Numerical<br>{len([f for f in features['new'] if f in features['numerical']])}",
        f"New Categorical<br>{len([f for f in features['new'] if f in features['categorical']])}",
        f"Maintained Numerical<br>{len([f for f in features['maintained'] if f in features['numerical']])}",
        f"Maintained Categorical<br>{len([f for f in features['maintained'] if f in features['categorical']])}"
    ])
    hover_data.extend([
        f"New numerical:<br>{format_feature_list([f for f in features['new'] if f in features['numerical']])}",
        f"New categorical:<br>{format_feature_list([f for f in features['new'] if f in features['categorical']])}",
        f"Maintained numerical:<br>{format_feature_list([f for f in features['maintained'] if f in features['numerical']])}",
        f"Maintained categorical:<br>{format_feature_list([f for f in features['maintained'] if f in features['categorical']])}"
    ])
    nodes_colors.extend([colors['new_features']] * 2 + [colors['preprocessing']] * 2)
    
    # Connect to engineering
    for i in range(4):
        source.append(base_idx + (i % 2))
        target.append(eng_idx + i)
        value.append(0.25)
    
    # Add processing nodes
    proc_idx = len(nodes_labels)
    nodes_labels.extend([
        f"StandardScaler<br>{len(features['numerical'])}",
        f"OneHotEncoder<br>{len(features['categorical'])}"
    ])
    hover_data.extend([
        f"Scaled features:<br>{format_feature_list(features['numerical'])}",
        f"Encoded features:<br>{format_feature_list(features['categorical'])}"
    ])
    nodes_colors.extend([colors['preprocessing']] * 2)
    
    # Connect to processing
    for i in range(4):
        source.append(eng_idx + i)
        target.append(proc_idx + (i % 2))
        value.append(0.25)
    # Add model nodes with metrics from CV results 
    model_idx = len(nodes_labels)
    for model_name in models:
        # Use CV metrics instead of test predictions
        cv_results = all_cv_results_df[all_cv_results_df['model'] == model_name]
        mse = -cv_results['mean_test_neg_mean_squared_error'].mean()
        r2 = cv_results['mean_test_r2'].mean()
        
        nodes_labels.append(f"{model_name}")
        hover_data.append(f"Model: {model_name}<br>MSE: {mse:.2e}<br>R²: {r2:.3f}")
        nodes_colors.append(colors['models'])
        source.extend([proc_idx, proc_idx + 1])
        target.extend([model_idx + list(models.keys()).index(model_name)] * 2)
        value.extend([0.4, 0.4])
    
    return nodes_labels, nodes_colors, hover_data, source, target, value


def add_model_table(fig, models, best_model_dict, param_grids, visible=True):
    """Add model parameter table"""
    best_params_formatted = []
    for model_name in models:
        # Best model parameters are extracted here
        best_params = best_model_dict[model_name].get_params()['model']
        params_str = "\n".join([f"{k}: {v}" for k, v in best_params.get_params().items() 
                              if k in param_grids[model_name]])
    
    fig.add_trace(
        go.Table(
            header=dict(
                values=['Model', 'Best Parameters'],
                font=dict(color='white', size=9),
                fill_color='#003f5c',
                align=['center', 'center'],
                height=18
            ),
            cells=dict(
                values=[list(models.keys()), best_params_formatted],
                align=['center', 'left'],
                font=dict(size=7),
                height=18
            ),
            columnwidth=[20, 80],
            visible=visible
        ),
        row=2, col=1
    )

def add_performance_heatmap(fig, metrics, models, visible=True):
    """Add model performance heatmap"""
    mse_min = min(metrics['mse'])
    mse_max = max(metrics['mse'])
    normalized_mse = [(x - mse_min) / (mse_max - mse_min) for x in metrics['mse']]
    
    model_scores = [[mse, r2] for mse, r2 in zip(normalized_mse, metrics['r2'])]
    
    fig.add_trace(
        go.Heatmap(
            z=model_scores,
            x=['MSE (normalized)', 'R²'],
            y=list(models.keys()),
            colorscale='RdYlBu_r',
            showscale=True,
            zmin=0,
            zmax=1,
            colorbar=dict(
                thickness=15,
                len=0.4,
                yanchor='bottom',
                y=0,
                ypad=0,
                xpad=10,
                x=1.05
            ),
            visible=visible
        ),
        row=2, col=4
    )

def create_model_metrics(cv_results, models):
    """Calculate model metrics"""
    metrics = {'mse': [], 'r2': []}
    for model in models:
        scores = cv_results[cv_results['model'] == model]
        # Best metrics are calculated here
        metrics['mse'].append(-scores['mean_test_neg_mean_squared_error'].mean())
        metrics['r2'].append(scores['mean_test_r2'].mean())
    return metrics

def add_target_selector(fig, targets, traces_per_target=3):
    """Add target selection dropdown with proper trace visibility"""
    
    def get_visibility_array(selected_target_idx, total_targets):
        """Generate visibility array for all traces"""
        visibility = []
        for target_idx in range(total_targets):
            # For each target we have 3 traces (Sankey, Table, Heatmap)
            visibility.extend([target_idx == selected_target_idx] * traces_per_target)
        return visibility
    
    buttons = [{
        'label': target,
        'method': 'update',
        'args': [
            {'visible': get_visibility_array(idx, len(targets))},
            {'title': f'Machine Learning Pipeline Analysis - {target}'}
        ]
    } for idx, target in enumerate(targets)]
    
    fig.update_layout(
        updatemenus=[{
            'buttons': buttons,
            'direction': 'down',
            'showactive': True,
            'x': 0.1,
            'y': 1.27,
            'xanchor': 'center',
            'yanchor': 'middle',
            'pad': {'r': 10, 'l': 10, 't': 10, 'b': 10}
        }],
        annotations=[{
            'text': "Target Variable:",
            'x': 0.02,
            'y': 1.27,
            'yanchor': 'middle',
            'xref': 'paper',
            'yref': 'paper',
            'showarrow': False
        }]
    )

def plot_linear_pipeline(df, df_transformed, models, param_grids, best_models_dict, all_cv_results_df, X_train_dict, targets):
    """Enhanced ML pipeline visualization with target selection"""
    # Create subplot layout
    fig = make_subplots(
        rows=2, cols=5,
        column_widths=[0.05, 0.40, 0.10, 0.40, 0.05],
        row_heights=[0.6, 0.4],
        specs=[
            [None, {"type": "sankey", "colspan": 3}, None, None, None],
            [{"type": "table", "colspan": 2}, None, None, {"type": "heatmap", "colspan": 2}, None]
        ]
    )
    
    # Define color scheme
    colors = {
        'primary': '#003f5c',
        'secondary': '#7a5195',
        'accent': '#ef5675',
        'stages': {
            'Raw Data': '#003f5c',
            'Features': '#7a5195',
            'Processing': '#ef5675',
            'Models': '#ffa600',
            'Output': '#ff7c43'
        },
        'preprocessing': '#66c2a5',
        'models': '#fc8d62',
        'new_features': '#ffa600'
    }
    
    
    # Process each target
    for idx, target in enumerate(targets):
        # Get feature data
        features = get_feature_data(df, df_transformed, X_train_dict, target)
        
        # Create Sankey nodes
        # Update call in plot_linear_pipeline
        nodes_data = create_sankey_nodes(
            features=features,
            models=models, 
            best_models_dict=best_models_dict,
            target=target,
            color_scheme=colors
        )
        # Add Sankey diagram
        fig.add_trace(
            go.Sankey(
                node=dict(
                    pad=20,
                    thickness=20,
                    line=dict(color="black", width=0.5),
                    label=nodes_data[0],  # nodes_labels
                    color=nodes_data[1],  # nodes_colors
                    customdata=nodes_data[2],  # hover_data
                    hovertemplate="%{customdata}<extra></extra>"
                ),
                link=dict(
                    source=nodes_data[3],  # source
                    target=nodes_data[4],  # target
                    value=nodes_data[5]    # value
                ),
                visible=(idx == 0)  # Only first target visible initially
            ),
            row=1, col=2
        )
        
        # Add model metrics
        metrics = create_model_metrics(
            all_cv_results_df[all_cv_results_df['target'] == target], 
            models
        )
        
        # Add parameter table and heatmap with visibility
        add_model_table(fig, models, best_models_dict[target], param_grids, visible=(idx == 0))
        add_performance_heatmap(fig, metrics, models, visible=(idx == 0))
    
    # Add target selector
    add_target_selector(fig, targets)
    
    # Update layout
    fig.update_layout(
        title=dict(
            text=f'Machine Learning Pipeline Analysis - {targets[0]}',
            x=0.5,
            y=0.95,
            xanchor='center',
            yanchor='top',
            font=dict(size=16)
        ),
        showlegend=False,
        template='plotly_white',
        font=dict(family='Arial', size=10),
        margin=dict(t=80, l=50, r=50, b=50)
    )
    
    return fig

# Generate visualization
pipeline_fig = plot_linear_pipeline(
    df=df,
    df_transformed=df_transformed, 
    models=models,
    param_grids=param_grids,
    best_models_dict=best_models_dict,
    all_cv_results_df=all_cv_results_df,
    X_train_dict=X_train_dict,
    targets=targets
)
pipeline_fig.show()

In [10]:
def plot_cv_results_detailed(cv_results_dict, targets):
    """
    Creates two types of plots for each target:
    1. Performance Plot: Shows MSE vs hyperparameters
    2. R² Score Plot: Shows R² vs hyperparameters
    """
    
    # Create separate figures for MSE and R²
    fig_mse = make_subplots(
        rows=1, cols=len(targets),
        subplot_titles=[f"{target} - Mean Squared Error" for target in targets],
        horizontal_spacing=0.15
    )
    
    fig_r2 = make_subplots(
        rows=1, cols=len(targets),
        subplot_titles=[f"{target} - R² Score" for target in targets],
        horizontal_spacing=0.15
    )

    # Professional color palette
    colors = {
        'ElasticNet': '#4267B2',
        'SVM': '#42B72A',
        'GradientBoosting': '#E94235',
        'RandomForest': '#7B68EE'
    }

    # Plot for each target
    for i, target in enumerate(targets, 1):
        target_cv_results = cv_results_dict[target]
        
        for model_name in colors.keys():
            model_results = target_cv_results[target_cv_results['model'] == model_name]
            
            if not model_results.empty:
                # Get scores and parameters
                mse_means = -model_results['mean_test_neg_mean_squared_error']
                r2_means = model_results['mean_test_r2']
                params = model_results['params'].apply(lambda x: {k.split('__')[1]: v for k, v in x.items()})
                
                # Create parameter labels
                param_labels = [f"Config {j+1}" for j in range(len(model_results))]
                
                # Add MSE trace
                fig_mse.add_trace(
                    go.Scatter(
                        x=param_labels,
                        y=mse_means,
                        name=model_name,
                        mode='lines+markers',
                        marker=dict(
                            size=10,
                            symbol='circle',
                            line=dict(width=2, color='white')
                        ),
                        line=dict(color=colors[model_name], width=2),
                        hovertemplate=(
                            f"<b>{model_name}</b><br>" +
                            "Parameters: %{text}<br>" +
                            "MSE: %{y:.4f}<extra></extra>"
                        ),
                        text=[str(p) for p in params]
                    ),
                    row=1, col=i
                )
                
                # Add R² trace
                fig_r2.add_trace(
                    go.Scatter(
                        x=param_labels,
                        y=r2_means,
                        name=model_name,
                        mode='lines+markers',
                        marker=dict(
                            size=10,
                            symbol='circle',
                            line=dict(width=2, color='white')
                        ),
                        line=dict(color=colors[model_name], width=2),
                        hovertemplate=(
                            f"<b>{model_name}</b><br>" +
                            "Parameters: %{text}<br>" +
                            "R²: %{y:.4f}<extra></extra>"
                        ),
                        text=[str(p) for p in params]
                    ),
                    row=1, col=i
                )

    # Update layouts
    for fig, title, yaxis in [(fig_mse, "MSE Across Model Configurations", "Mean Squared Error"),
                             (fig_r2, "R² Scores Across Model Configurations", "R² Score")]:
        fig.update_layout(
            height=600,
            width=1200,
            title=dict(
                text=title,
                x=0.5,
                y=0.95,
                font=dict(size=24)
            ),
            template='plotly_white',
            showlegend=True,
            legend=dict(
                orientation="h",
                yanchor="bottom",
                y=-0.3,
                xanchor="center",
                x=0.5
            ),
            margin=dict(t=100, b=100)
        )
        
        # Update axes for all subplots
        for j in range(1, len(targets) + 1):
            fig.update_xaxes(
                row=1, col=j,
                title="Hyperparameter Configurations",
                tickangle=45,
                showgrid=True,
                gridwidth=1,
                gridcolor='rgba(0,0,0,0.1)'
            )
            fig.update_yaxes(
                row=1, col=j,
                title=yaxis,
                showgrid=True,
                gridwidth=1,
                gridcolor='rgba(0,0,0,0.1)'
            )

    return fig_mse, fig_r2

# Store results by target
cv_results_dict = {}
all_cv_results = []

for target in targets:
    target_cv_results = all_cv_results_df[all_cv_results_df['target'] == target]
    cv_results_dict[target] = target_cv_results

# Create and display the plots
fig_mse, fig_r2 = plot_cv_results_detailed(cv_results_dict, targets)
fig_mse.show()
fig_r2.show()

In [11]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np

# Enhanced color palette
colors = ['#1f77b4', '#ff7f0e', '#2ca02c', '#d62728', '#9467bd', '#8c564b', '#e377c2', '#7f7f7f']

# Create figures for model performance visualization with better spacing
fig_metrics = make_subplots(
    rows=2, cols=2,
    subplot_titles=("Mean Squared Error", "Root Mean Squared Error", 
                   "Mean Absolute Error", "R² Score"),
    vertical_spacing=0.2,
    horizontal_spacing=0.15
)

# Calculate metrics and store
metrics_data = {target: {
    'model_names': [],
    'mse': [],
    'rmse': [],
    'mae': [], 
    'r2': []
} for target in targets}

# Calculate metrics with enhanced visualization data
for target in targets:
    X_test = X_test_dict[target]
    y_test = y_test_dict[target]
    
    for idx, (model_name, model) in enumerate(best_models_dict[target].items()):
        y_pred = model.predict(X_test)
        
        metrics_data[target]['model_names'].append(model_name)
        metrics_data[target]['mse'].append(mean_squared_error(y_test, y_pred))
        metrics_data[target]['rmse'].append(np.sqrt(mean_squared_error(y_test, y_pred)))
        metrics_data[target]['mae'].append(mean_absolute_error(y_test, y_pred))
        metrics_data[target]['r2'].append(r2_score(y_test, y_pred))

# Enhanced bar plots with distinct colors and better spacing
for i, target in enumerate(targets):
    for metric, row, col in [('mse', 1, 1), ('rmse', 1, 2), ('mae', 2, 1), ('r2', 2, 2)]:
        fig_metrics.add_trace(
            go.Bar(
                name=f"{target}",
                x=metrics_data[target]['model_names'],
                y=metrics_data[target][metric],
                marker_color=[colors[j + i*len(metrics_data[target]['model_names'])] 
                            for j in range(len(metrics_data[target]['model_names']))],
                text=np.round(metrics_data[target][metric], 3),
                textposition='outside',
                showlegend=(row == 1 and col == 1),
                legendgroup=target,  # Link traces with same target
                visible='legendonly' if i > 0 else True  # Show first target by default
            ),
            row=row, col=col
        )

# Enhanced metrics layout
fig_metrics.update_layout(
    height=1000,  # Increased height for better readability
    title={
        'text': "Model Performance Metrics Comparison",
        'y': 0.97,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top',
        'font': dict(size=24)
    },
    barmode='group',
    template='plotly_white',
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="center",
        x=0.5
    ),
    showlegend=True,
    font=dict(size=12)
)

# Update axes with better formatting
for i in range(1, 3):
    for j in range(1, 3):
        fig_metrics.update_xaxes(row=i, col=j, tickangle=45)

fig_metrics.update_xaxes(title_text="Models", row=2, col=1, title_font=dict(size=14))
fig_metrics.update_xaxes(title_text="Models", row=2, col=2, title_font=dict(size=14))
fig_metrics.update_yaxes(title_text="MSE", row=1, col=1, title_font=dict(size=14))
fig_metrics.update_yaxes(title_text="RMSE", row=1, col=2, title_font=dict(size=14))
fig_metrics.update_yaxes(title_text="MAE", row=2, col=1, title_font=dict(size=14))
fig_metrics.update_yaxes(title_text="R² Score", row=2, col=2, title_font=dict(size=14))

fig_metrics.show()

# Enhanced Actual vs Predicted plots
fig_pred = make_subplots(
    rows=1, cols=2,
    subplot_titles=[f"Actual vs Predicted - {target}" for target in targets],
    horizontal_spacing=0.2,
    specs=[[{"secondary_y": True}, {"secondary_y": True}]]
)

# Custom function for creating a gradient colormap
def create_gradient_colormap(n_colors):
    return [f'rgb({int(255*(1-i/n_colors))},{int(255*0.3)},{int(255*i/n_colors)})' 
            for i in range(n_colors)]

for i, target in enumerate(targets, 1):
    X_test = X_test_dict[target]
    y_test = y_test_dict[target]
    
    model_colors = create_gradient_colormap(len(best_models_dict[target]))
    
    for idx, (model_name, model) in enumerate(best_models_dict[target].items()):
        y_pred = model.predict(X_test)
        
        fig_pred.add_trace(
            go.Scatter(
                x=y_test,
                y=y_pred,
                mode='markers',
                name=model_name,
                marker=dict(
                    size=8,
                    color=model_colors[idx],
                    opacity=0.7,
                    line=dict(color='white', width=1)
                ),
                hovertemplate=(
                    f"<b>{model_name}</b><br>" +
                    "Actual: %{x:,.2f}<br>" +
                    "Predicted: %{y:,.2f}<br>" +
                    "Error: %{customdata:,.2f}<extra></extra>"
                ),
                customdata=np.abs(y_test - y_pred),
                showlegend=True,
                legend=f"legend{i}"  # Assign to specific legend
            ),
            row=1, col=i,
            secondary_y=False
        )
    

# Enhanced prediction plot layout
fig_pred.update_layout(
    height=700,
    title={
        'text': "Model Predictions vs Actual Values",
        'y': 0.95,
        'x': 0.5,
        'xanchor': 'center',
        'yanchor': 'top',
        'font': dict(size=24)
    },
    template='plotly_white',
    showlegend=True,
    legend1=dict(
        x=0.25,
        y=-0.15,  # Adjust first row y position
        xanchor='center',
        yanchor='top',
        orientation='h',
        bgcolor='rgba(255,255,255,0.9)',
        bordercolor='rgba(0,0,0,0.2)',
        borderwidth=1,
        traceorder='normal'
    ),
    legend2=dict(
        x=0.75,
        y=-0.15,  # Match first row y position
        xanchor='center',
        yanchor='top',
        orientation='h',
        bgcolor='rgba(255,255,255,0.9)', 
        bordercolor='rgba(0,0,0,0.2)',
        borderwidth=1,
        traceorder='normal'
    ),
    margin=dict(b=150)  # Increase bottom margin to accommodate two-row legends
)

# Update axes labels and format
for i in range(1, 3):
    fig_pred.update_xaxes(
        col=i,
        title=dict(text="Actual Values", font=dict(size=14)),
        gridcolor='rgba(0,0,0,0.1)',
        showgrid=True
    )
    fig_pred.update_yaxes(
        col=i,
        title=dict(text="Predicted Values", font=dict(size=14)),
        gridcolor='rgba(0,0,0,0.1)',
        showgrid=True
    )

fig_pred.show()

In [12]:
def plot_feature_importance(model, preprocessor, X_train):
    """Plot feature importance with proper dimension handling"""
    # Get feature names first
    feature_names = []
    for name, transformer, cols in preprocessor.transformers_:
        if name == 'num':
            feature_names.extend(cols)
        elif name == 'cat':
            # Get one-hot encoded feature names
            encoder = transformer.named_steps['onehot']
            encoder.fit(X_train[cols])
            feature_names.extend(encoder.get_feature_names_out(cols))
    
    # Get importances based on model type
    if hasattr(model, 'feature_importances_'):
        importances = model.feature_importances_
    elif hasattr(model, 'coef_'):
        importances = np.abs(model.coef_)
        if importances.ndim > 1:
            importances = importances.flatten()
    else:
        raise ValueError("Model does not provide feature importances")
        
    # Ensure dimensions match
    if len(feature_names) != len(importances):
        raise ValueError(f"Feature names ({len(feature_names)}) and importances ({len(importances)}) dimensions mismatch")
        
    # Create DataFrame with aligned data
    importance_df = pd.DataFrame({
        'feature': feature_names,
        'importance': importances
    })
    
    # Aggregate and sort
    importance_df = (importance_df.groupby('feature')['importance']
                    .sum()
                    .sort_values(ascending=False)
                    .reset_index())
    
    # Add cumulative importance
    importance_df['cumulative'] = importance_df['importance'].cumsum() / importance_df['importance'].sum()
    
    # Filter to top 95% contributors
    return importance_df[importance_df['cumulative'] <= 0.95]

# Create visualization
def create_importance_plot(feature_importance_data, targets, models):
    """Create interactive feature importance plot with target selection"""
    
    # Create base figure
    fig = go.Figure()
    
    # Add traces for each combination
    initial_target = targets[0]
    initial_model = models[0]
    
    for target in targets:
        for model_name in models:
            data = feature_importance_data[target][model_name]
            fig.add_trace(go.Bar(
                x=data['feature'],
                y=data['importance'],
                name=f"{target} - {model_name}",
                visible=(target == initial_target and model_name == initial_model)
            ))
    
    # Create model dropdown buttons
    model_buttons = [{
        'label': model,
        'method': 'update',
        'args': [
            {'visible': [
                t == initial_target and m == model 
                for t in targets 
                for m in models
            ]},
            {'title': f"Feature Importance: {initial_target} ({model})"}
        ]
    } for model in models]
    
    # Create target dropdown buttons
    target_buttons = [{
        'label': target,
        'method': 'update',
        'args': [
            {'visible': [
                t == target and m == initial_model 
                for t in targets 
                for m in models
            ]},
            {'title': f"Feature Importance: {target} ({initial_model})"}
        ]
    } for target in targets]
    
    # Update layout with both dropdowns
    fig.update_layout(
        updatemenus=[
            # Model selector
            {
                'buttons': model_buttons,
                'direction': 'down',
                'showactive': True,
                'x': 0.1,
                'xanchor': 'center',
                'y': 1.27,
                'yanchor': 'middle'
            },
            # Target selector
            {
                'buttons': target_buttons,
                'direction': 'down',
               'showactive': True,
                'x': 0.3,
                'xanchor': 'center',
                'y': 1.27,
                'yanchor': 'middle'
            }
        ],
        title=f"Feature Importance: {initial_target} ({initial_model})",
        xaxis_title="Features",
        yaxis_title="Importance",
        showlegend=False
    )
    
    return fig

# Generate data and plot
feature_importance_data = {
    target: {
        model: plot_feature_importance(
            best_models_dict[target][model].named_steps['model'],
            best_models_dict[target][model].named_steps['preprocessor'],
            X_train_dict[target]
        )
        for model in models
    }
    for target in targets
}

fig = create_importance_plot(feature_importance_data, targets, list(models.keys()))
fig.show()

In [13]:
import plotly.express as px
import plotly.graph_objects as go
import numpy as np
import scipy.stats as stats

# Function to plot residuals using Plotly
def plot_residuals(y_test, y_pred, title):
    residuals = y_test - y_pred
    
    # Residuals vs Predicted Values
    fig = px.scatter(x=y_pred, y=residuals, labels={'x': 'Predicted Values', 'y': 'Residuals'}, title=title)
    fig.add_hline(y=0, line_dash="dash", line_color="red")
    fig.show()
    
    # Histogram of Residuals
    fig = px.histogram(residuals, nbins=30, title=f'Histogram of Residuals for {title}')
    fig.show()
    
    # Q-Q Plot
    qq = stats.probplot(residuals, dist="norm", plot=None)
    qq_fig = go.Figure()
    qq_fig.add_trace(go.Scatter(x=qq[0][0], y=qq[0][1], mode='markers', name='Residuals'))
    qq_fig.add_trace(go.Scatter(x=qq[0][0], y=qq[0][0], mode='lines', name='Reference Line'))
    qq_fig.update_layout(title=f'Q-Q Plot of Residuals for {title}', xaxis_title='Theoretical Quantiles', yaxis_title='Sample Quantiles')
    qq_fig.show()

# Create dropdown options for models and targets
model_options_residual = ['ElasticNet', 'SVM', 'GradientBoosting', 'RandomForest']
targets_residual = ['TotalEnergy(kBtu)', 'TotalGHGEmissions']

# Generate residual data for each model and target combination
residual_data = {}
X_test_dict = {}
y_test_dict = {}
for target in targets_residual:
    residual_data[target] = {}
    X_test_dict[target] = X_test  # Assuming X_test is defined elsewhere
    y_test_dict[target] = y_test  # Assuming y_test is defined elsewhere
    for model in model_options_residual:
        y_pred = best_models_dict[target][model].predict(X_test_dict[target])
        residuals = y_test_dict[target] - y_pred
        residual_data[target][model] = residuals

        
# Create the initial figure with the first target and model
initial_target = targets_residual[0]
initial_model = model_options_residual[0]
initial_residuals = residual_data[initial_target][initial_model]
y_pred_initial = best_models_dict[initial_target][initial_model].predict(X_test_dict[initial_target])

# Create figures for residuals, histogram, and Q-Q plot
fig_residuals = go.Figure()
fig_histogram = go.Figure()
fig_qq = go.Figure()

# Add traces for each target and model combination
for target in targets_residual:
    for model in model_options_residual:
        residuals = residual_data[target][model]
        y_pred = best_models_dict[target][model].predict(X_test_dict[target])
        
        # Residuals vs Predicted Values
        fig_residuals.add_trace(go.Scatter(
            x=y_pred,
            y=residuals,
            mode='markers',
            name=f"{target} - {model} Residuals vs Predicted",
            visible=(target == initial_target and model == initial_model)
        ))
        
        # Histogram of Residuals
        fig_histogram.add_trace(go.Histogram(
            x=residuals,
            nbinsx=30,
            name=f"{target} - {model} Histogram",
            visible=(target == initial_target and model == initial_model)
        ))
        
        # Q-Q Plot
        qq = stats.probplot(residuals, dist="norm", plot=None)
        trace_index = len(fig_qq.data)  # Get current trace index
        fig_qq.add_trace(go.Scatter(
            x=qq[0][0],
            y=qq[0][1],
            mode='markers',
            name=f"{target} - {model} Q-Q Plot",
            visible=(target == initial_target and model == initial_model)
        ))
        fig_qq.add_trace(go.Scatter(
            x=qq[0][0],
            y=qq[0][0],
            mode='lines',
            name=f"{target} - {model} Q-Q Reference Line",
            visible=(target == initial_target and model == initial_model)
        ))

# Create dropdown menu for model selection
model_dropdown_buttons = [
    {
        'args': [
            {
                'visible': [model == m for t in targets_residual for m in model_options_residual]
            }
        ],
        'label': model,
        'method': 'update'
    }
    for model in model_options_residual
]

# Create dropdown menu for target selection
target_dropdown_buttons = [
    {
        'args': [
            {
                'visible': [target == t for t in targets_residual for m in model_options_residual]
            }
        ],
        'label': target,
        'method': 'update'
    }
    for target in targets_residual
]
# Create dropdown menu for Q-Q plot model selection
qq_model_dropdown_buttons = [
    {
        'args': [
            {
                'visible': [i//2 == m_idx for i in range(len(fig_qq.data))]
            }
        ],
        'label': model,
        'method': 'update'
    }
    for m_idx, model in enumerate(model_options_residual)
]

# Create dropdown menu for Q-Q plot target selection
qq_target_dropdown_buttons = [
    {
        'args': [
            {
                'visible': [i//2 >= t_idx*len(model_options_residual) and i//2 < (t_idx+1)*len(model_options_residual) for i in range(len(fig_qq.data))]
            }
        ],
        'label': target,
        'method': 'update'
    }
    for t_idx, target in enumerate(targets_residual)
]

# Add dropdown menus to the figures
for fig in [fig_residuals, fig_histogram]:
    fig.update_layout(
        updatemenus=[
            dict(
                type="buttons",
                direction="left",
                buttons=model_dropdown_buttons,
                pad={"r": 8, "t": 8},
                showactive=True,
                x=0.7,
                xanchor="center",
                y=1.1,
                yanchor="middle"
            ),
            dict(
                type="buttons",
                direction="left",
                buttons=target_dropdown_buttons,
                pad={"r": 5, "t": 8},
                showactive=True,
                x=0.7,
                xanchor="center",
                y=1.25,
                yanchor="middle"
            ),
        ],
        showlegend=True  # Enable the legend
    )

# Separate layout for Q-Q plot
fig_qq.update_layout(
    updatemenus=[
        dict(
            type="buttons",
            direction="left",
            buttons=qq_model_dropdown_buttons,
            pad={"r": 8, "t": 8},
            showactive=True,
            x=0.7,
            xanchor="center",
            y=1.1,
            yanchor="middle"
        ),
        dict(
            type="buttons",
            direction="left",
            buttons=qq_target_dropdown_buttons,
            pad={"r": 5, "t": 8},
            showactive=True,
            x=0.7,
            xanchor="center",
            y=1.25,
            yanchor="middle"
        ),
    ],
    showlegend=True,
    title=f"Q-Q Plot of Residuals"
)

# Set titles for each figure
fig_residuals.update_layout(title=f"Residual Analysis")
fig_histogram.update_layout(title=f"Histogram of Residuals")
fig_qq.update_layout(title=f"Q-Q Plot of Residuals")

# Display the figures
fig_residuals.show()
fig_histogram.show()
fig_qq.show()

c:\git\Mission4\venv_mission4\Lib\site-packages\sklearn\utils\validation.py:2739: UserWarning:

X does not have valid feature names, but OneHotEncoder was fitted with feature names

c:\git\Mission4\venv_mission4\Lib\site-packages\sklearn\utils\validation.py:2739: UserWarning:

X does not have valid feature names, but OneHotEncoder was fitted with feature names

c:\git\Mission4\venv_mission4\Lib\site-packages\sklearn\utils\validation.py:2739: UserWarning:

X does not have valid feature names, but OneHotEncoder was fitted with feature names

c:\git\Mission4\venv_mission4\Lib\site-packages\sklearn\utils\validation.py:2739: UserWarning:

X does not have valid feature names, but OneHotEncoder was fitted with feature names

c:\git\Mission4\venv_mission4\Lib\site-packages\sklearn\utils\validation.py:2739: UserWarning:

X does not have valid feature names, but OneHotEncoder was fitted with feature names

c:\git\Mission4\venv_mission4\Lib\site-packages\sklearn\utils\validation.py:2739: UserWarn

In [14]:
from sklearn.model_selection import learning_curve
import plotly.graph_objects as go
import plotly.express as px
import numpy as np

def plot_learning_curves(best_models_dict, X_test_dict, y_test_dict, model_options, targets):
    fig = go.Figure()
    
    # Professional color palette with rgba values
    colors = {
        'ElasticNet': 'rgba(66, 103, 178, 1)',
        'SVM': 'rgba(66, 183, 42, 1)',
        'GradientBoosting': 'rgba(233, 66, 53, 1)',
        'RandomForest': 'rgba(123, 104, 238, 1)'
    }
    
    # Function to create transparent version of color
    def make_transparent(rgba_str, alpha):
        return rgba_str.replace('1)', f'{alpha})')
    
    for target in targets:
        X = X_train_dict[target]
        y = y_train_dict[target]
        
        for model_name in model_options:
            train_sizes, train_scores, test_scores = learning_curve(
                best_models_dict[target][model_name],
                X, y,
                train_sizes=np.linspace(0.1, 1.0, 10),
                cv=5,
                scoring='neg_mean_squared_error',
                n_jobs=-1
            )
            
            # Calculate means and std
            train_mean = -np.mean(train_scores, axis=1)
            train_std = np.std(train_scores, axis=1)
            test_mean = -np.mean(test_scores, axis=1)
            test_std = np.std(test_scores, axis=1)
            
            visible = (target == targets[0] and model_name == model_options[0])
            
            # Training curve
            fig.add_trace(go.Scatter(
                x=train_sizes,
                y=train_mean,
                name=f"{model_name} (Training)",
                mode='lines+markers',
                line=dict(color=colors[model_name], width=3),
                visible=visible,
                hovertemplate="<b>%{text}</b><br>Size: %{x}<br>MSE: %{y:.4f}<extra></extra>",
                text=[f"{model_name} - Training"]*len(train_sizes)
            ))
            
            # Training confidence band
            fig.add_trace(go.Scatter(
                x=np.concatenate([train_sizes, train_sizes[::-1]]),
                y=np.concatenate([train_mean + train_std, (train_mean - train_std)[::-1]]),
                fill='tonexty',
                fillcolor=make_transparent(colors[model_name], 0.2),
                line=dict(width=0),
                showlegend=False,
                visible=visible,
                hoverinfo='skip'
            ))
            
            # Validation curve
            fig.add_trace(go.Scatter(
                x=train_sizes,
                y=test_mean,
                name=f"{model_name} (Validation)",
                mode='lines+markers',
                line=dict(color=colors[model_name], width=3, dash='dash'),
                visible=visible,
                hovertemplate="<b>%{text}</b><br>Size: %{x}<br>MSE: %{y:.4f}<extra></extra>",
                text=[f"{model_name} - Validation"]*len(train_sizes)
            ))
            
            # Validation confidence band
            fig.add_trace(go.Scatter(
                x=np.concatenate([train_sizes, train_sizes[::-1]]),
                y=np.concatenate([test_mean + test_std, (test_mean - test_std)[::-1]]),
                fill='tonexty',
                fillcolor=make_transparent(colors[model_name], 0.1),
                line=dict(width=0),
                showlegend=False,
                visible=visible,
                hoverinfo='skip'
            ))
    # Create buttons for model selection
    model_buttons = [dict(
        args=[{"visible": [i//4 == m_idx for i in range(len(fig.data))]}],
        label=model,
        method="update"
    ) for m_idx, model in enumerate(model_options)]
    
    # Create buttons for target selection
    target_buttons = [dict(
        args=[{"visible": [i//4 >= t_idx*len(model_options) and i//4 < (t_idx+1)*len(model_options) 
               for i in range(len(fig.data))]}],
        label=target,
        method="update"
    ) for t_idx, target in enumerate(targets)]
    
    # Update layout
    fig.update_layout(
        height=700,
        title=dict(
            text="Learning Curves Analysis",
            x=0.5,
            y=0.95,
            xanchor='center',
            yanchor='top',
            font=dict(size=24)
        ),
        xaxis=dict(
            title="Training Set Size",
            titlefont=dict(size=16),
            gridcolor='rgba(0,0,0,0.1)',
            type='log'
        ),
        yaxis=dict(
            title="Mean Squared Error",
            titlefont=dict(size=16),
            gridcolor='rgba(0,0,0,0.1)',
            type='log'
        ),
        template='plotly_white',
        showlegend=True,
        legend=dict(
            orientation="h",
            yanchor="bottom",
            y=-0.3,
            xanchor="center",
            x=0.5
        ),
        updatemenus=[
            dict(
                buttons=model_buttons,
                direction="down",
                showactive=True,
                x=0.25,
                y=1.1,
                xanchor="center",
                yanchor="middle"
            ),
            dict(
                buttons=target_buttons,
                direction="down",
                showactive=True,
                x=0.05,
                y=1.1,
                xanchor="center",
                yanchor="middle"
            )
        ],
        margin=dict(t=150)
    )
    
    return fig

# Create and display the learning curves
fig_learning = plot_learning_curves(
    best_models_dict=best_models_dict,
    X_test_dict=X_test_dict,
    y_test_dict=y_test_dict,
    model_options=model_options_residual,
    targets=targets_residual
)
fig_learning.show()